# Setup

In [ ]:
!pip install nltk
!pip install random
!pip install spellchecker
!pip install pyspellchecker
!pip install bpe
!nvidia-smi

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
ERROR: Could not find a version that satisfies the requirement random (from versions: none)
ERROR: No matching distribution found for random
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 3.9 MB 4.0 MB/s 
  Created wheel for spellchecker: filename=spellchecker-0.4-py3-none-any.whl size=3966515 sha256=db1e66eb6dbd109e85c505ed81e66edaf1d416d803db7f5c535d0d9b59cd1c96
  Stored in directory: /root/.cache/pip/wheels/58/e9/48/b82b733a7a0a9cc52ed239ccf082ff33e2fbda71670ddd3349
  Created wheel for inexactsearch: filename=inexactsearch-1.0.2-py3-none-any.whl size=7141 sha256=df38d24a6db31efbcc7a99f4d976543461f5d5ac95be034b89da4776b5a6025b
  Stored in directory: /root/.cache/pip/wheels/3c/f3/5d/77e8983e86af1c3c6

# Importing important packages

In [ ]:
import nltk
nltk.download('punkt')
from nltk import word_tokenize
import random
from spellchecker import SpellChecker
import re
from typing import Dict, Tuple
from bpe import Encoder

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


# Loading dataset

In [ ]:
                                        # ParSQuAD
# automatic
  # Train : 
            # https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1
  # Dev : 
            # https://www.dropbox.com/s/iz7xzp9zrdgau5w/dev-v2.0.json?dl=1
# manual
  # Train : 
            # https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1
  # Dev : 
            # https://www.dropbox.com/s/iz7xzp9zrdgau5w/dev-v2.0.json?dl=1
# ------------------------------------------------------------------------------
                                        # pquad_public
  # Train :
            # https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1
  # Test :
            # https://www.dropbox.com/s/drhtfb6sfvjn1ic/test-v2.0.json?dl=1
  # Dev :
            # https://www.dropbox.com/s/iz7xzp9zrdgau5w/dev-v2.0.json?dl=1
# ------------------------------------------------------------------------------
                                        # PersianQA
  # Train : 
            # https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1
  # Dev : 
            # https://www.dropbox.com/s/iz7xzp9zrdgau5w/dev-v2.0.json?dl=1
!mkdir dataset \
&& cd dataset \
&& wget https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1 \
&& wget https://www.dropbox.com/s/iz7xzp9zrdgau5w/dev-v2.0.json?dl=1
# Loading dataset
file_train = open("/content/dataset/train-v2.0.json?dl=1", "r")
train = file_train.read()
file_dev = open("/content/dataset/dev-v2.0.json?dl=1", "r")
dev = file_dev.read()

--2022-06-23 17:51:31--  https://www.dropbox.com/s/63l6iv2sz9ui8ld/train-v2.0.json?dl=1
Resolving www.dropbox.com (www.dropbox.com)... 162.125.1.18, 2620:100:6016:18::a27d:112
Connecting to www.dropbox.com (www.dropbox.com)|162.125.1.18|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /s/dl/63l6iv2sz9ui8ld/train-v2.0.json [following]
--2022-06-23 17:51:31--  https://www.dropbox.com/s/dl/63l6iv2sz9ui8ld/train-v2.0.json
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://ucd742c85df223233f62025da259.dl.dropboxusercontent.com/cd/0/get/BnzE8vvWbrEN2NWZTuhApbIv0xMlRHE030BkopCjgP3W6_-RsIFdYWRJscUU-HbnEeuBAxgb87Rn1K6QQ5eN0bRQc1rQc1vYanKV8uQ7AFfQBqPMfdLSyyI-AXrv9EYBePaoqsBh4NWRhKNHaXpb6e7nd1vvOkHtA0bvNvSoPb6qor-EVSUCtC9fJUNlGi7ZGjQ/file?dl=1# [following]
--2022-06-23 17:51:31--  https://ucd742c85df223233f62025da259.dl.dropboxusercontent.com/cd/0/get/BnzE8vvWbrEN2NWZTuhApbIv0xMlRHE030Bk

In [ ]:
train

'{\n  "data": [\n    {\n      "title": "شرکت فولاد مبارکه اصفهان",\n      "paragraphs": [\n        {\n          "qas": [\n            {\n              "answers": [\n                {\n                  "answer_start": 114,\n                  "answer_end": 131,\n                  "text": "در شرق شهر مبارکه"\n                }\n              ],\n              "question": "شرکت فولاد مبارکه در کجا واقع شده است",\n              "is_impossible": false,\n              "id": 1\n            },\n            {\n              "answers": [\n                {\n                  "answer_start": 263,\n                  "answer_end": 264,\n                  "text": "۶"\n                }\n              ],\n              "question": "فولاد مبارکه چند بار برنده جایزه شرکت دانشی را کسب کرده است؟",\n              "is_impossible": false,\n              "id": 2\n            },\n            {\n              "answers": [\n                {\n                  "answer_start": 413,\n                  "answer_end

# Text Pre-Processing

**0-** *BPE (Byte Pair Encoding)*

  **A-** *Implement BPE manually*

In [ ]:
# Find all unique letters in the corpus
def Find_Vocabulary(Dictionary):
    Vocabulary = []
    for word in Dictionary:
        for string in word:
            Vocabulary.append(string)
    Vocabulary = list(dict.fromkeys(Vocabulary))
    Vocabulary.remove(' ')
    return Vocabulary

# Find all most frequent pairs in the corpus
def Find_Most_Frequent_Pair(My_Dictionary: Dict[str, int]) -> Dict[Tuple[str, str], int]:
    Pair = {}
    for Vocab, Frequency in My_Dictionary.items():
        Letter = Vocab.split()
        for i in range(len(Letter) - 1):
            pair = (Letter[i], Letter[i + 1])
            New_Frequency = Pair.get(pair, 0)
            Pair[pair] = New_Frequency + Frequency
    return Pair

# Merge most frequent Consecutive letters into one word
def Combine_Vocabulary(Most_Frequent_Pair: Tuple[str, str], Input_Vocabulary: Dict[str, int]) -> Dict[str, int]:
    Merged_Vocabulary = {}
    pattern = re.escape(' '.join(Most_Frequent_Pair))
    Substitution = ''.join(Most_Frequent_Pair)
    for Input_Word in Input_Vocabulary:
        Output_Word = re.sub(pattern, Substitution, Input_Word)
        Merged_Vocabulary[Output_Word] = Input_Vocabulary[Input_Word]
    return Merged_Vocabulary

  **B-** *Implement BPE using library*

In [ ]:
encoder = Encoder(200, pct_bpe=0.88)  # params chosen for demonstration purposes
encoder.fit(train.split('\n'))

In [ ]:
# Let's see an example
example = "Let's see an example ."
print(encoder.tokenize(example))
print(next(encoder.transform([example])))
print(next(encoder.inverse_transform(encoder.transform([example]))))

['__sow', 'l', 'e', 't', '__eow', '__sow', '__unk', '__eow', '__sow', 's', '__eow', '__sow', 'se', 'e', '__eow', '__sow', 'an', '__eow', '__sow', 'ex', 'a', '__unk', '__unk', 'l', 'e', '__eow', '.']
[25, 83, 40, 43, 24, 25, 0, 24, 25, 51, 24, 25, 105, 40, 24, 25, 99, 24, 25, 88, 47, 0, 0, 83, 40, 24, 20]
let __unk s see an exa__unk__unkle .


**1-** *Lowercasing*

In [ ]:
# Lowercasing source dataset
train = train.lower()
dev = dev.lower()

**2-** *Remove Extra Whitespaces*

In [ ]:
def remove_whitespace(text):
    return  " ".join(text.split())

# Removing Extra Whitespaces 
train = remove_whitespace(train)
dev = remove_whitespace(dev)

**3-** *Tokenization*

In [ ]:
# Tokenization of source dataset
train_token = word_tokenize(train)
dev_token = word_tokenize(dev)

In [ ]:
# Let's take a look at some random tokens
print("Some of the tokens at the train data set :")
print(random.choices(train_token, k=10))
print("Some of the tokens at the dev data set :")
print(random.choices(dev_token, k=10))

Some of the tokens at the train data set :
["''", 'حرفه', 'هستی', 'کاهش', 'answer_end', 'آن', ',', 'دوچرخه', '``', 'id']
Some of the tokens at the dev data set :
[':', ':', 'فرا', ',', 'آن', 'answer_start', ',', '``', 'و', ',']


**4-** *Spelling Correction*

In [ ]:
def spell_check(text):
    result = []
    spell = SpellChecker()
    for word in text:
        correct_word = spell.correction(word)
        result.append(correct_word)
    return result

# Spelling Correction 
train_split = train.split() 
#train_Spelling_Correction = spell_check(train_split)
dev_split = dev.split() 
#dev_Spelling_Correction = spell_check(dev_split)

In [ ]:
# Let's try an example of spelling correction
text = "confuson matrx".split() 
spell_check(text)

['confusion', 'matrix']

**5-** *Removal of Tags*

In [ ]:
def remove_tag(text):
    text=' '.join(text)
    html_pattern = re.compile('<.*?>')
    return html_pattern.sub(r'', text)

# Removal of Tags of source dataset
train_ = remove_tag(train.split())
dev = remove_tag(dev.split())

In [ ]:
# Let's see an example of "Removal of Tags"
text = "<HEAD> this is head tag </HEAD>" 
print("The input text is :")
print(text,"\n")
print("The output text after removing tags is :")
print(remove_tag(text.split()))

The input text is :
<HEAD> this is head tag </HEAD> 

The output text after removing tags is :
 this is head tag 


In [ ]:
!git clone https://github.com/huggingface/transformers \
&& cd transformers \
&& git checkout a3085020ed0d81d4903c50967687192e3101e770 

Cloning into 'transformers'...
remote: Enumerating objects: 99108, done.
remote: Counting objects: 100% (263/263), done.
remote: Compressing objects: 100% (151/151), done.
remote: Total 99108 (delta 134), reused 151 (delta 84), pack-reused 98845
Receiving objects: 100% (99108/99108), 92.75 MiB | 25.21 MiB/s, done.
Resolving deltas: 100% (72980/72980), done.
Note: checking out 'a3085020ed0d81d4903c50967687192e3101e770'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by performing another checkout.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -b with the checkout command again. Example:

  git checkout -b <new-branch-name>

HEAD is now at a3085020e Added repetition penalty to PPLM example (#2436)


In [ ]:
!pip install ./transformers
!pip install tensorboardX

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Processing ./transformers
  DEPRECATION: A future pip version will change local packages to be built in-place without first copying to a temporary directory. We recommend you use --use-feature=in-tree-build to test your packages with this new behavior before it becomes the default.
   pip 21.3 will remove support for this functionality. You can find discussion regarding this at https://github.com/pypa/pip/issues/7555.
     |████████████████████████████████| 4.7 MB 7.0 MB/s 
     |████████████████████████████████| 132 kB 56.5 MB/s 
     |████████████████████████████████| 1.2 MB 55.3 MB/s 
     |████████████████████████████████| 880 kB 61.2 MB/s 
     |████████████████████████████████| 8.9 MB 55.9 MB/s 
     |████████████████████████████████| 79 kB 10.2 MB/s 
     |████████████████████████████████| 138 kB 80.8 MB/s 
     |████████████████████████████████| 127 kB 77.0 MB/s 
  Created wheel f

# Train Model

**Get Training and Evaluation Data**

**Run training**

In [ ]:
!export SQUAD_DIR=/content/dataset \
&& python transformers/examples/run_squad.py \
  --model_type albert \
  --model_name_or_path albert-base-v2 \
  --do_train \
  --do_eval \
  --do_lower_case \
  --train_file $SQUAD_DIR/train-v2.0.json?dl=1 \
  --predict_file $SQUAD_DIR/dev-v2.0.json?dl=1 \
  --per_gpu_train_batch_size 12 \
  --learning_rate 3e-5 \
  --num_train_epochs 1.0 \
  --max_seq_length 384 \
  --doc_stride 128 \
  --output_dir /content/model_output \
  --save_steps 1000 \
  --threads 4 \
  --version_2_with_negative 

06/23/2022 17:52:43 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 1, distributed training: False, 16-bits training: False
06/23/2022 17:52:43 - INFO - transformers.file_utils -   https://s3.amazonaws.com/models.huggingface.co/bert/albert-base-v2-config.json not found in cache or force_download set to True, downloading to /root/.cache/torch/transformers/tmpifaledzb
Downloading: 100% 684/684 [00:00<00:00, 462kB/s]
06/23/2022 17:52:43 - INFO - transformers.file_utils -   storing https://s3.amazonaws.com/models.huggingface.co/bert/albert-base-v2-config.json in cache at /root/.cache/torch/transformers/0bbb1531ce82f042a813219ffeed7a1fa1f44cd8f78a652c47fc5311e0d40231.978ff53dd976bbf4bc66f09bf4205da0542be753d025263787842df74d15bbca
06/23/2022 17:52:43 - INFO - transformers.file_utils -   creating metadata file for /root/.cache/torch/transformers/0bbb1531ce82f042a813219ffeed7a1fa1f44cd8f78a652c47fc5311e0d40231.978ff53dd976bbf4bc66f09bf4205da0542be753d025263787842df74d15bbca
06

# Setup prediction code

In [ ]:
import os
import torch
import time
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler

from transformers import (
    AlbertConfig,
    AlbertForQuestionAnswering,
    AlbertTokenizer,
    squad_convert_examples_to_features
)

from transformers.data.processors.squad import SquadResult, SquadV2Processor, SquadExample

from transformers.data.metrics.squad_metrics import compute_predictions_logits

# READER NOTE: Set this flag to use own model, or use pretrained model in the Hugging Face repository
use_own_model = False

if use_own_model:
  model_name_or_path = "/content/model_output"
else:
  model_name_or_path = "ktrapeznikov/albert-xlarge-v2-squad-v2"

output_dir = ""

# Config
n_best_size = 1
max_answer_length = 30
do_lower_case = True
null_score_diff_threshold = 0.0

def to_list(tensor):
    return tensor.detach().cpu().tolist()

# Setup model
config_class, model_class, tokenizer_class = (
    AlbertConfig, AlbertForQuestionAnswering, AlbertTokenizer)
config = config_class.from_pretrained(model_name_or_path)
tokenizer = tokenizer_class.from_pretrained(
    model_name_or_path, do_lower_case=True)
model = model_class.from_pretrained(model_name_or_path, config=config)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model.to(device)

processor = SquadV2Processor()

def run_prediction(question_texts, context_text):
    """Setup function to compute predictions"""
    examples = []

    for i, question_text in enumerate(question_texts):
        example = SquadExample(
            qas_id=str(i),
            question_text=question_text,
            context_text=context_text,
            answer_text=None,
            start_position_character=None,
            title="Predict",
            is_impossible=False,
            answers=None,
        )

        examples.append(example)

    features, dataset = squad_convert_examples_to_features(
        examples=examples,
        tokenizer=tokenizer,
        max_seq_length=384,
        doc_stride=128,
        max_query_length=64,
        is_training=False,
        return_dataset="pt",
        threads=1,
    )

    eval_sampler = SequentialSampler(dataset)
    eval_dataloader = DataLoader(dataset, sampler=eval_sampler, batch_size=10)

    all_results = []

    for batch in eval_dataloader:
        model.eval()
        batch = tuple(t.to(device) for t in batch)

        with torch.no_grad():
            inputs = {
                "input_ids": batch[0],
                "attention_mask": batch[1],
                "token_type_ids": batch[2],
            }

            example_indices = batch[3]

            outputs = model(**inputs)

            for i, example_index in enumerate(example_indices):
                eval_feature = features[example_index.item()]
                unique_id = int(eval_feature.unique_id)

                output = [to_list(output[i]) for output in outputs]

                start_logits, end_logits = output
                result = SquadResult(unique_id, start_logits, end_logits)
                all_results.append(result)

    output_prediction_file = "predictions.json"
    output_nbest_file = "nbest_predictions.json"
    output_null_log_odds_file = "null_predictions.json"

    predictions = compute_predictions_logits(
        examples,
        features,
        all_results,
        n_best_size,
        max_answer_length,
        do_lower_case,
        output_prediction_file,
        output_nbest_file,
        output_null_log_odds_file,
        False,  # verbose_logging
        True,  # version_2_with_negative
        null_score_diff_threshold,
        tokenizer,
    )

    return predictions

Downloading:   0%|          | 0.00/717 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/760k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/235M [00:00<?, ?B/s]

# Run predictions

In [ ]:
context = "New Zealand (Māori: Aotearoa) is a sovereign island country in the southwestern Pacific Ocean. It has a total land area of 268,000 square kilometres (103,500 sq mi), and a population of 4.9 million. New Zealand's capital city is Wellington, and its most populous city is Auckland."
questions = ["How many people live in New Zealand?", 
             "What's the largest city?"]

# Run method
predictions = run_prediction(questions, context)

# Print results
for key in predictions.keys():
  print(predictions[key])

add example index and unique id: 100%|██████████| 2/2 [00:00<00:00, 23497.50it/s]


4.9 million.
Auckland
